In [1]:
from __future__ import print_function

import sys
import json
import keras
import numpy as np
from keras.datasets import mnist, cifar10
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.optimizers import SGD

Using TensorFlow backend.


__使用keras中的mnist及cifar10。__

In [2]:
epochs = 1000
num_classes = 0
image_size = 0
image_channel = 0
data_set = ''

__全域變數們，所有訓練最多到1000epochs，並在training step設定early stopping。__

In [3]:
def set_cifar10():
    global image_size, image_channel, num_classes, data_set
    data_set = 'cifar10'
    image_size = 32
    image_channel = 3
    num_classes = 10
    (x_train, y_train), (x_test, y_test) = cifar10.load_data()
    x_train = scale_pixel_value(np.reshape(crop_image(x_train, crop_size), 
                                       [-1, (image_size - crop_size**2)**2 * image_channel]))
    num_train = x_train.shape[0]
    image_size = image_size - crop_size**2
    return x_train, y_train, x_test, y_test

def set_mnist():
    global image_size, image_channel, num_classes, data_set
    data_set = 'mnist'
    image_size = 28
    image_channel = 1
    num_classes = 10
    (x_train, y_train), (x_test, y_test) = mnist.load_data()
    x_train = x_train.reshape(x_train.shape[0], image_size**2 * image_channel)
    x_train = x_train.astype('float32')
    x_train /= 255
    x_test = x_test.reshape(x_test.shape[0], image_size**2 * image_channel)
    x_test = x_test.astype('float32')
    x_test /= 255
    return x_train, y_train, x_test, y_test
    
def crop_image(images, c):
    images = images[:, c:image_size-c, c:image_size-c]
    return images

def scale_pixel_value(images):
    return images/255.

def partially_corrupted_label(label, probability):
    pcl = []
    for l in label:
        if np.random.random_sample() <= probability:
            pcl.append(np.random.randint(0, num_classes))
        else:
            pcl.append(l)
    return np.array(pcl)

def random_label(label):
    return np.reshape(np.random.randint(num_classes, size=len(label)), [-1,])

def label_similarity(label1, label2):
    counter = 0
    print(label1.shape, label2.shape)
    for l1, l2 in zip(label1, label2):
        if l1 != l2:
            counter += 1
    return (len(label1) - float(counter)) / len(label1)

def shuffled_pixel(images):
    shuffled_images = []
    permutation = np.random.permutation(image_size**2 * image_channel)
    for image in images:
        shuffled_image = []
        for p in permutation:
            shuffled_image.append(image[p])
        shuffled_images.append(shuffled_image)
    return np.array(shuffled_images)

def gaussian(images, proportion):
    pixel_num = len(images) * (image_size**2 * image_channel)
    pixel = np.reshape(images, [pixel_num])
    mean = pixel.mean()
    variance_sum = np.ndarray.sum((pixel - mean)**2)
    standard_deviation = np.sqrt(variance_sum / pixel_num)
    temp = np.array(np.random.normal(loc=mean, scale=standard_deviation, 
                                     size=[(int)(len(images)*proportion), (image_size**2 * image_channel)]))
    temp = temp.clip(0.0, 1.0)
    return np.concatenate((images[:(int)(len(images)*(1 - proportion))], temp))
    
def random_pixel(images):
    random_pixel_images = []
    for image in images:
        random_pixel_image = []
        np.random.shuffle(image)
        random_pixel_images.append(image)
    return np.array(random_pixel_images)

#### 重現實驗中所需要的functions
#### Fitting random labels

- True labels: the original dataset without modification.
- Partially corrupted labels: independently with probability p, the label of each image is corrupted as a uniform random class.
- Random labels: all the labels are replaced with random ones.

#### Fitting random pixels

- Shuffled pixels: a random permutation of the pixels is chosen and then the same permutation is applied to all the images in both training and test set.
- Random pixels: a different random permutation is applied to each image independently.

#### 將gaussian加入proportion

- Gaussian: A Gaussian distribution (with matching mean and variance to the original image dataset) is used to generate random pixels for each image.

In [4]:
def train(x_train, y_train, x_test, y_test, batch_size, hidden_size, layer, learning_rate, gaussian=False, proportion=0):
    
    y_train = keras.utils.to_categorical(y_train, num_classes)
    y_test = keras.utils.to_categorical(y_test, num_classes)

    model = Sequential()
    model.add(Dense(hidden_size, activation='relu', input_shape=(image_size**2 * image_channel,)))
    
    for i in xrange(layer-1):
        model.add(Dense(hidden_size, activation='relu'))
        #model.add(Dropout(0.2))
    
    model.add(Dense(10, activation='softmax'))
    model.summary()
    
    model.compile(loss='categorical_crossentropy',
                  optimizer=SGD(lr=learning_rate),
                  metrics=['accuracy'])

    callbacks = [keras.callbacks.EarlyStopping(monitor='val_loss',patience=20,verbose=0)]
    history = model.fit(x_train, y_train,
                        batch_size=batch_size,
                        epochs=epochs,
                        verbose=1,
                        validation_data=(x_test, y_test)
                       )
    
    score = model.evaluate(x_test, y_test, verbose=0)
    
    if gaussian is False:
        with open('./%s/batch_size_%d_layer_%d_hidden_size_%d_summary' % (data_set, batch_size, layer, hidden_size), 'w') as fout:
            orig_stdout = sys.stdout
            sys.stdout = fout
            print(model.summary())
            sys.stdout = orig_stdout
    else:
        with open('./%s/gaussian_%f_batch_size_%d_layer_%d_hidden_size_%d_summary' % (data_set, proportion, batch_size, layer, hidden_size), 'w') as fout:
            orig_stdout = sys.stdout
            sys.stdout = fout
            print(model.summary())
            sys.stdout = orig_stdout
            fout.write('score: %f %f\r\n' % (score[0], score[1]))
        
    return history.history

In [ ]:
x_train , y_train, x_test, y_test = set_mnist()
batch_size = 1024
learning_rate = 0.01
hidden_size = [16, 128, 512, 1024]
layer = [2, 4, 6, 8, 10]
'''
for i in xrange(3):
    for size in hidden_size:
        for l in layer:
            print('hidden_size: %d layer: %d' % (size, l))
            history = train(x_train, y_train, x_test, y_test, batch_size=batch_size, hidden_size=size, layer=l, learning_rate=learning_rate)
            with open('./%s/%d_batch_size_%d_layer_%d_hidden_size_%d' % (data_set, i+1, batch_size, l, size), 'w') as fout:
                json.dump(history, fout)
    break
'''
'''
for i in xrange(3):
    for size in hidden_size:
        for l in layer:
            print('random label hidden_size: %d layer: %d' % (size, l))
            history = train(x_train, random_label(y_train), x_test, y_test, batch_size=batch_size, hidden_size=size, layer=l, learning_rate=learning_rate)
            with open('./%s/%d_random_label_batch_size_%d_layer_%d_hidden_size_%d' % (data_set, i+1, batch_size, l, size), 'w') as fout:
                json.dump(history, fout)
    break
'''

gaussian_proportion = [.0, .2, .4, .6, .8, 1.]
hidden_size = [16, 512, 1024]
layer = [2, 4, 8]
for i in xrange(3):
    for proportion in gaussian_proportion:
        for size in hidden_size:
            for l in layer:
                print('gaussian: %f hidden_size: %d layer: %d' % (proportion, size, l))
                history = train(gaussian(x_train, proportion), y_train, x_test, y_test, batch_size=batch_size, hidden_size=size, layer=l, learning_rate=learning_rate, gaussian=True, proportion=proportion)
                with open('./%s/%d_gaussian_%f_batch_size_%d_layer_%d_hidden_size_%d' % (data_set, i+1, proportion, batch_size, l, size), 'w') as fout:
                    json.dump(history, fout)
    break

hidden_size = 512
layer = 3
for i in xrange(3):
    for proportion in gaussian_proportion:
            print('gausson: %f hidden_size: %d layer: %d' % (proportion, size, l))
            history = train(gaussian(x_train, proportion), random_label(y_train), x_test, y_test, batch_size=batch_size, hidden_size=hidden_size, layer=layer, learning_rate=learning_rate)
            with open('./%s/random_label_gaussian_%f_batch_size_%d_layer_%d_hidden_size_%d' % (data_set, proportion, batch_size, layer, hidden), 'w') as fout:
                json.dump(history, fout)
    break

random label hidden_size: 512 layer: 2
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 512)               401920    
_________________________________________________________________
dense_2 (Dense)              (None, 512)               262656    
_________________________________________________________________
dense_3 (Dense)              (None, 10)                5130      
Total params: 669,706
Trainable params: 669,706
Non-trainable params: 0
_________________________________________________________________
Train on 60000 samples, validate on 10000 samples
Epoch 1/1000
60000/60000 [==============================] - 1s - loss: 2.3147 - acc: 0.0999 - val_loss: 2.2939 - val_acc: 0.1049
Epoch 2/1000
60000/60000 [==============================] - 0s - loss: 2.3113 - acc: 0.0995 - val_loss: 2.2934 - val_acc: 0.1094
Epoch 3/1000
60000/60000 [===========================

60000/60000 [==============================] - 0s - loss: 2.2912 - acc: 0.1270 - val_loss: 2.2977 - val_acc: 0.1125
Epoch 58/1000
60000/60000 [==============================] - 0s - loss: 2.2911 - acc: 0.1269 - val_loss: 2.2979 - val_acc: 0.1129
Epoch 59/1000
60000/60000 [==============================] - 0s - loss: 2.2909 - acc: 0.1284 - val_loss: 2.2982 - val_acc: 0.1127
Epoch 60/1000
60000/60000 [==============================] - 0s - loss: 2.2906 - acc: 0.1288 - val_loss: 2.2976 - val_acc: 0.1113
Epoch 61/1000
60000/60000 [==============================] - 0s - loss: 2.2905 - acc: 0.1292 - val_loss: 2.2979 - val_acc: 0.1131
Epoch 62/1000
60000/60000 [==============================] - 0s - loss: 2.2902 - acc: 0.1293 - val_loss: 2.2975 - val_acc: 0.1123
Epoch 63/1000
60000/60000 [==============================] - 0s - loss: 2.2900 - acc: 0.1298 - val_loss: 2.2975 - val_acc: 0.1122
Epoch 64/1000
60000/60000 [==============================] - 0s - loss: 2.2898 - acc: 0.1296 - val_loss:

60000/60000 [==============================] - 0s - loss: 2.2799 - acc: 0.1443 - val_loss: 2.2991 - val_acc: 0.1114
Epoch 120/1000
60000/60000 [==============================] - 0s - loss: 2.2797 - acc: 0.1443 - val_loss: 2.2997 - val_acc: 0.1127
Epoch 121/1000
60000/60000 [==============================] - 0s - loss: 2.2796 - acc: 0.1448 - val_loss: 2.2990 - val_acc: 0.1126
Epoch 122/1000
60000/60000 [==============================] - 0s - loss: 2.2794 - acc: 0.1455 - val_loss: 2.2993 - val_acc: 0.1132
Epoch 123/1000
60000/60000 [==============================] - 0s - loss: 2.2792 - acc: 0.1451 - val_loss: 2.2995 - val_acc: 0.1111
Epoch 124/1000
60000/60000 [==============================] - 0s - loss: 2.2790 - acc: 0.1450 - val_loss: 2.2995 - val_acc: 0.1108
Epoch 125/1000
60000/60000 [==============================] - 0s - loss: 2.2789 - acc: 0.1455 - val_loss: 2.2993 - val_acc: 0.1120
Epoch 126/1000
60000/60000 [==============================] - 0s - loss: 2.2787 - acc: 0.1458 - va

60000/60000 [==============================] - 0s - loss: 2.2692 - acc: 0.1581 - val_loss: 2.2992 - val_acc: 0.1128
Epoch 182/1000
60000/60000 [==============================] - 0s - loss: 2.2690 - acc: 0.1580 - val_loss: 2.2999 - val_acc: 0.1160
Epoch 183/1000
60000/60000 [==============================] - 0s - loss: 2.2689 - acc: 0.1581 - val_loss: 2.2999 - val_acc: 0.1162
Epoch 184/1000
60000/60000 [==============================] - 0s - loss: 2.2687 - acc: 0.1584 - val_loss: 2.2994 - val_acc: 0.1153
Epoch 185/1000
60000/60000 [==============================] - 0s - loss: 2.2685 - acc: 0.1584 - val_loss: 2.3001 - val_acc: 0.1165
Epoch 186/1000
60000/60000 [==============================] - 0s - loss: 2.2684 - acc: 0.1590 - val_loss: 2.3001 - val_acc: 0.1161
Epoch 187/1000
60000/60000 [==============================] - 0s - loss: 2.2682 - acc: 0.1590 - val_loss: 2.3000 - val_acc: 0.1177
Epoch 188/1000
60000/60000 [==============================] - 0s - loss: 2.2680 - acc: 0.1598 - va

60000/60000 [==============================] - 0s - loss: 2.2579 - acc: 0.1702 - val_loss: 2.3017 - val_acc: 0.1163
Epoch 244/1000
60000/60000 [==============================] - 0s - loss: 2.2577 - acc: 0.1709 - val_loss: 2.3017 - val_acc: 0.1157
Epoch 245/1000
60000/60000 [==============================] - 0s - loss: 2.2575 - acc: 0.1702 - val_loss: 2.3012 - val_acc: 0.1191
Epoch 246/1000
60000/60000 [==============================] - 0s - loss: 2.2573 - acc: 0.1704 - val_loss: 2.3029 - val_acc: 0.1195
Epoch 247/1000
60000/60000 [==============================] - 0s - loss: 2.2572 - acc: 0.1714 - val_loss: 2.3017 - val_acc: 0.1156
Epoch 248/1000
60000/60000 [==============================] - 0s - loss: 2.2569 - acc: 0.1716 - val_loss: 2.3013 - val_acc: 0.1156
Epoch 249/1000
60000/60000 [==============================] - 0s - loss: 2.2567 - acc: 0.1718 - val_loss: 2.3016 - val_acc: 0.1161
Epoch 250/1000
60000/60000 [==============================] - 0s - loss: 2.2565 - acc: 0.1719 - va

...

60000/60000 [==============================] - 0s - loss: 0.0062 - acc: 1.0000 - val_loss: 0.1595 - val_acc: 0.9742
Epoch 530/1000
60000/60000 [==============================] - 0s - loss: 0.0062 - acc: 1.0000 - val_loss: 0.1595 - val_acc: 0.9742
Epoch 531/1000
60000/60000 [==============================] - 0s - loss: 0.0061 - acc: 1.0000 - val_loss: 0.1595 - val_acc: 0.9742
Epoch 532/1000
60000/60000 [==============================] - 0s - loss: 0.0061 - acc: 1.0000 - val_loss: 0.1596 - val_acc: 0.9744
Epoch 533/1000
60000/60000 [==============================] - 0s - loss: 0.0060 - acc: 1.0000 - val_loss: 0.1598 - val_acc: 0.9743
Epoch 534/1000
60000/60000 [==============================] - 0s - loss: 0.0060 - acc: 1.0000 - val_loss: 0.1598 - val_acc: 0.9746
Epoch 535/1000
60000/60000 [==============================] - 0s - loss: 0.0059 - acc: 1.0000 - val_loss: 0.1600 - val_acc: 0.9741
Epoch 536/1000
60000/60000 [==============================] - 0s - loss: 0.0059 - acc: 1.0000 - va

60000/60000 [==============================] - 0s - loss: 0.0041 - acc: 1.0000 - val_loss: 0.1652 - val_acc: 0.9742
Epoch 592/1000
60000/60000 [==============================] - 0s - loss: 0.0040 - acc: 1.0000 - val_loss: 0.1654 - val_acc: 0.9744
Epoch 593/1000
60000/60000 [==============================] - 0s - loss: 0.0040 - acc: 1.0000 - val_loss: 0.1656 - val_acc: 0.9744
Epoch 594/1000
60000/60000 [==============================] - 0s - loss: 0.0040 - acc: 1.0000 - val_loss: 0.1655 - val_acc: 0.9743
Epoch 595/1000
60000/60000 [==============================] - 0s - loss: 0.0040 - acc: 1.0000 - val_loss: 0.1657 - val_acc: 0.9742
Epoch 596/1000
60000/60000 [==============================] - 0s - loss: 0.0039 - acc: 1.0000 - val_loss: 0.1658 - val_acc: 0.9743
Epoch 597/1000
60000/60000 [==============================] - 0s - loss: 0.0039 - acc: 1.0000 - val_loss: 0.1659 - val_acc: 0.9740
Epoch 598/1000
60000/60000 [==============================] - 0s - loss: 0.0039 - acc: 1.0000 - va

60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1696 - val_acc: 0.9742
Epoch 654/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1698 - val_acc: 0.9741
Epoch 655/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1698 - val_acc: 0.9741
Epoch 656/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1700 - val_acc: 0.9741
Epoch 657/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1697 - val_acc: 0.9742
Epoch 658/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1701 - val_acc: 0.9743
Epoch 659/1000
60000/60000 [==============================] - 0s - loss: 0.0029 - acc: 1.0000 - val_loss: 0.1701 - val_acc: 0.9743
Epoch 660/1000
60000/60000 [==============================] - 0s - loss: 0.0028 - acc: 1.0000 - va

60000/60000 [==============================] - 0s - loss: 0.0023 - acc: 1.0000 - val_loss: 0.1729 - val_acc: 0.9739
Epoch 716/1000
60000/60000 [==============================] - 0s - loss: 0.0023 - acc: 1.0000 - val_loss: 0.1731 - val_acc: 0.9739
Epoch 717/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - val_loss: 0.1731 - val_acc: 0.9744
Epoch 718/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - val_loss: 0.1731 - val_acc: 0.9740
Epoch 719/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - val_loss: 0.1732 - val_acc: 0.9740
Epoch 720/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - val_loss: 0.1733 - val_acc: 0.9742
Epoch 721/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - val_loss: 0.1732 - val_acc: 0.9742
Epoch 722/1000
60000/60000 [==============================] - 0s - loss: 0.0022 - acc: 1.0000 - va

60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1757 - val_acc: 0.9742
Epoch 778/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1757 - val_acc: 0.9742
Epoch 779/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1758 - val_acc: 0.9740
Epoch 780/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1759 - val_acc: 0.9739
Epoch 781/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1759 - val_acc: 0.9741
Epoch 782/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1760 - val_acc: 0.9739
Epoch 783/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - val_loss: 0.1760 - val_acc: 0.9737
Epoch 784/1000
60000/60000 [==============================] - 0s - loss: 0.0018 - acc: 1.0000 - va